# Description

This notebook takes in the sim_cahce file from the benrules_v2 simulator that runs random simulations on a given number of satellites.  We will extract the satellite data from all the the run simulations and combine into a single pandas dataframe. \

First part of the notebook is dedicated to visualizing satellite position over time.

# Imports

In [1]:
# Data Processing Libraries
import numpy as np
import pandas as pd
# Randomization Libraries to Select Random Points in the simulation.
import random
# Libraries for file reading
import h5py
# Bokeh and plotting related imports
# Plotting Imports
import bokeh.io
bokeh.io.output_notebook()  # Set plot output to embed in notebook.
import bokeh.layouts
import bokeh.plotting
# Other imports for multi-plot figures.
from bokeh.io import output_file, show
from bokeh.layouts import column
from bokeh.plotting import figure
# Memory management libraries for Python
import gc
# Progress Bar Libraries
from tqdm import tqdm

Loading BokehJS ...

In [2]:
# Remove max columns and row limit on pandas
pd.options.display.max_columns = None
pd.options.display.max_rows = 50000

# Setup Plotting Functions

In [3]:
from bokeh.palettes import Turbo256 as palette
import itertools
from random import randint

def plot_2D_body_time_series(pos_x_list, pos_y_list, plot_width, plot_height, title):
    """
    Accepts lists for x and y dimensions whose elements are time series data and whose
    index represents the number of the body in the simulation.
    
    returns Bokeh figure to plot.
    """
    # Create Bokeh figure to add plots to
    f = bokeh.plotting.figure(
        title = title,
        plot_width = plot_width,
        plot_height = plot_height
    )

    # Generate line for each body.
    # Randomly select color from palette using randint
    for i in range(0,len(pos_x_list)):
        f.line(
            pos_x_list[i],
            pos_y_list[i],
            line_width = 1,
            color = palette[randint(0,255)],
            legend_label = str(i)
        )
    f.legend.location = 'top_left'
    return f

def two_dim_numpy_data_to_2D_pos_list(sat_pos_list):
    """
    Take in a list of satellite position data and split into X and Y position data lists for 
    each dimension.
    """
    pos_x_list = []
    pos_y_list = []
    # Take the 2D (X and Y) time series elements of the sat_pos_list and split into the 
    # Pos_x and Pos_y lists
    for satellite_pos in sat_pos_list:
        temp_x_time_series = satellite_pos[:,0]
        temp_y_time_series = satellite_pos[:,1]
        pos_x_list.append(temp_x_time_series)
        pos_y_list.append(temp_y_time_series)
    return pos_x_list, pos_y_list

def plot_data_conv_3D_np_pos_to_2D_pos_list(pos_np_array):
    """
    Accepts 3D position numpy array and extracts the time steps for each body from 
    the numpy array.  Adds those time series for each dimension to a list of 1D numpy arrays.
    """
    # List of bodies for each dimension whose elements are numpy arrays going back in time.  
    # Each element is a time series for that body and that body's dimension.
    pos_x_list = []
    pos_y_list = []
    # First index of the numpy array is the time step and second is the body number.  Will loop
    # over all bodies and slice out the time steps for each body.
    for current_body_index in range(0, pos_np_array.shape[1]):
        # Get slice of data to create time series of position values
        # Use .to_numpy() to convert to numpy array
        temp_x_time_series = pos_np_array[:, current_body_index, 0]
        temp_y_time_series = pos_np_array[:, current_body_index, 1]
        # Add time series to respective dimension.
        pos_x_list.append(temp_x_time_series)
        pos_y_list.append(temp_y_time_series)
    
    # TODO: Continue with this function to get the position data plotted.
    return pos_x_list, pos_y_list

# Read in HDF5 Files to Lists of Numpy Arrays

In [4]:
# Set folder to read hdf5 cache file from.
in_data_folder = "input_data/"
# Body index in the numpy arrays from the simulation that designates the satellite from 
# the planets
sat_index: int = 10
# Lists for storing the satellite data from each simulation in the cache.
acc_list = []
vel_list = []
pos_list = []
dis_list = []
mass_list = []

# Open the sim_cache, get the data groups, and extract datasets from it.
with h5py.File(in_data_folder + 'sim_cache.hdf5', 'r') as f:
    # Get all the groups and data_set keys
    group_keys = []
    for key in f.keys():
        group_keys.append(key)
    # Loop over all groups in the dataset and extract the numpy arrays
    for group_name in group_keys:
        group = f[group_name]
        # Grab the raw data from the file.
        temp_acc = group['acc'][()]
        temp_vel = group['vel'][()]
        temp_pos = group['pos'][()]
        temp_dis = group['dis'][()]
        temp_mass = group['mass'][()]
        # Extract the Satellite data only
        # Only grabbing X and Y dimensions
        temp_acc = temp_acc[:, sat_index, 0:2]
        temp_vel = temp_vel[:, sat_index, 0:2]
        temp_pos = temp_pos[:, sat_index, 0:2]
        temp_dis = temp_dis[:, sat_index, 0:2]
        temp_mass = temp_mass[sat_index, 0]
        
        acc_list.append(temp_acc)
        vel_list.append(temp_vel)
        pos_list.append(temp_pos)
        dis_list.append(temp_dis)
        mass_list.append(temp_mass)

In [5]:
pos_list[0]

array([[ 1.4235496e+11, -4.6388589e+10],
       [ 1.4230756e+11, -4.6467047e+10],
       [ 1.4226067e+11, -4.6547157e+10],
       ...,
       [ 5.2233671e+10, -1.0899438e+11],
       [ 5.2115038e+10, -1.0901300e+11],
       [ 5.1996353e+10, -1.0903151e+11]], dtype=float32)

In [6]:
pos_list[0][:,0].shape

(39998,)

In [7]:
mass_list

[442.0, 1643.0, 3794.0, 1969.0, 223.0, 2652.0, 1338.0, 2512.0, 1422.0, 3110.0]

# Plot the path of the Specified Satellite

In [8]:
# Convert all the satellite data to a list of time series for plotting.
# Will plot all satellites on the same plot.
pos_x_list, pos_y_list = two_dim_numpy_data_to_2D_pos_list(pos_list)

In [9]:
# Plot the converted data.
fig = plot_2D_body_time_series(
    pos_x_list = pos_x_list,
    pos_y_list = pos_y_list,
    plot_width = 800,
    plot_height = 800,
    title = "Paths of All Satellites for All Simulations"
)

bokeh.plotting.show(fig)

# Plot the Whole Universe with its Associated Satellite

Get the position data for the specified satellite and its universe and plot it.

In [10]:
# Set folder to read hdf5 cache file from.
in_data_folder = "input_data/"
# Index for the simulation to grab
sim_index: int = 0
# Lists for storing the satellite data from each simulation in the cache.
raw_pos_np = None

# Open the sim_cache, get the data groups, and extract datasets from it.
with h5py.File(in_data_folder + 'sim_cache.hdf5', 'r') as f:
    # Get data group for the specified index
    group_key = 'sim_' + str(sim_index)
    # Grab the position data for all bodies in that group.
    group = f[group_key]
    # Grab the raw data from the file.
    raw_pos_np = group['pos'][()]
# Convert to list of time series for plotting.  
pos_x_list, pos_y_list = plot_data_conv_3D_np_pos_to_2D_pos_list(raw_pos_np)
del raw_pos_np
# Plot the converted data.
fig = plot_2D_body_time_series(
    pos_x_list = pos_x_list,
    pos_y_list = pos_y_list,
    plot_width = 800,
    plot_height = 800,
    title = "Path of sat {} with Universe".format(sim_index)
)

bokeh.plotting.show(fig)

# Convert Acceleration, Velocity, Displacement, and Position Numpy Arrays to Pandas Dataframes

In [11]:
# Set the number of "shotgun" future time steps to predict.
num_ts_to_predict = 20

### Converting Acceleration to Pandas DataFrame

In [12]:
acc_list[0]

array([[ 0.05497216, -0.62425435],
       [ 0.04210711, -0.13789415],
       [ 0.02056709, -0.05923451],
       ...,
       [-0.00392823,  0.00819288],
       [-0.00392267,  0.00820128],
       [-0.00391709,  0.0082097 ]], dtype=float32)

In [13]:
# Stack all the satellites as bodies into a single numpy array.
stacked_raw_acc = np.stack(acc_list, axis=1)
stacked_raw_acc.shape

(39998, 10, 2)

In [14]:
# Construct the acceleration dataframe from the raw simulator velocity output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
acc_m,acc_n,acc_r = stacked_raw_acc.shape
# Stack the XY or XYZ arrays of each body into columns, removing a dimension.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Had to add 1 to arange to go from 1 to 79 instead of 0.
acc_arr = np.column_stack(
    (np.repeat(np.arange(1, acc_m+1, 1),acc_n), 
     np.tile(np.arange(0,acc_n,1),acc_m), 
     stacked_raw_acc[:,:,0:2].reshape(acc_m*acc_n,-1))
)

# Create dataframe from stacked column array.
acc_df = pd.DataFrame(acc_arr)
# Delete intermediate numpy arrays and original data from memory.
del acc_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
acc_df = acc_df.groupby([0,1]).mean()
acc_df.index.names = ['time_step', 'body']
acc_df.columns = ['acc_x', 'acc_y']
# Swapping to time_step then body to keep compatibility with existing code.
#acc_df = acc_df.swaplevel('time_step', 'body').sort_index(level=0)
#acc_df.head(15)
idx = pd.IndexSlice
acc_df.loc[idx[1, :], :]

acc_x     acc_y
time_step body                    
1.0       0.0   0.054972 -0.624254
          1.0  -0.050005 -0.317740
          2.0  -0.104679 -0.475992
          3.0  -0.066227 -0.467194
          4.0  -0.112355 -0.456318
          5.0  -0.092108 -0.547595
          6.0  -0.046654 -0.368221
          7.0  -0.087844 -0.441338
          8.0  -0.189189 -0.602040
          9.0  -0.148280 -0.585344

In [15]:
# Drop the time steps that could not be used for calculating displacecment.
# Create list of time steps to drop.
beg_drop_index = max(acc_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(acc_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
# Drop the time steps from the displacement dataframe.
acc_df.drop(drop_list, level=0, inplace=True)
# Ouput the new dataframe
acc_df.head(10)

acc_x     acc_y
time_step body                    
1.0       0.0   0.054972 -0.624254
          1.0  -0.050005 -0.317740
          2.0  -0.104679 -0.475992
          3.0  -0.066227 -0.467194
          4.0  -0.112355 -0.456318
          5.0  -0.092108 -0.547595
          6.0  -0.046654 -0.368221
          7.0  -0.087844 -0.441338
          8.0  -0.189189 -0.602040
          9.0  -0.148280 -0.585344

In [16]:
acc_df.shape

(399780, 2)

### Converting Velocity to Pandas DataFrame

Dataframes are really slow.  We will need to calculate the future velocities for num_ts_to_predict so that we can shotgun predict multiple time steps at the same time.  We want to do this with numpy arrays before converting to a pandas dataframe for easy grouping and indexing. \
Will first need to go through and calculate the future time steps to shotgun-predict.

In [17]:
vel_list[0]

array([[-13297.586 , -21158.062 ],
       [-13095.398 , -22052.777 ],
       [-12995.508 , -22351.068 ],
       ...,
       [-32920.21  ,  -5183.9585],
       [-32934.34  ,  -5154.4463],
       [-32948.45  ,  -5124.9033]], dtype=float32)

In [18]:
# Stack all the satellites as bodies into a single numpy array.
stacked_raw_vel = np.stack(vel_list, axis=1)
stacked_raw_vel.shape

(39998, 10, 2)

In [19]:
# Create a numpy array with the same first 2 dimensions of the input data (time steps and num bodies)
# the number of columns will be the same as the number of time steps
# being predicted multiplied by the dimensions (2) (X and Y)
vel_pred_cache = np.full(
    (stacked_raw_vel.shape[0], stacked_raw_vel.shape[1], num_ts_to_predict*2),
    np.nan,
    dtype=np.float32
)
# Loop over all time steps in the numpy array.
# Grab groups of bodies from future time steps
for curr_time_step in tqdm(range(0, stacked_raw_vel.shape[0])):
    # Loop over the number of time steps in the future to be grabbing
    # velocities from.
    # Don't do last time steps for displacement dataframe.  Can only look so many
    # time steps into the future before running out of data.
    if curr_time_step < (stacked_raw_vel.shape[0] - num_ts_to_predict):
        for num_ts_in_future in range(1, num_ts_to_predict + 1):
            vel_pred_cache[int(curr_time_step), :, int(2*num_ts_in_future-2):int(2*num_ts_in_future)] = \
            stacked_raw_vel[int(curr_time_step + num_ts_in_future), :, 0:2]
            
# Concatenate the cached numpy array to the original velocity dataset
stacked_raw_vel = np.concatenate((stacked_raw_vel[:,:,0:2], vel_pred_cache), axis=2)
# Delete the cache.
del vel_pred_cache
gc.collect()
#Display first portion of the dataframe
pd.DataFrame(stacked_raw_vel[0])

100%|██████████| 39998/39998 [00:01<00:00, 31094.22it/s]


0             1             2             3             4  \
0 -13297.585938 -21158.062500 -13095.398438 -22052.777344 -12995.507812   
1 -10903.631836 -16621.818359 -10942.112305 -17066.871094 -10955.525391   
2 -11333.654297 -19078.960938 -11393.473633 -19781.359375 -11394.704102   
3 -11700.374023 -18999.427734 -11716.444336 -19674.957031 -11707.301758   
4 -11116.695312 -18852.402344 -11192.368164 -19527.167969 -11200.546875   
5 -11867.745117 -19856.552734 -11885.129883 -20666.884766 -11863.637695   
6 -11375.381836 -17585.041016 -11397.356445 -18104.480469 -11401.579102   
7 -11276.567383 -18649.560547 -11327.403320 -19291.912109 -11331.137695   
8 -11494.234375 -20361.787109 -11606.954102 -21308.888672 -11597.722656   
9 -11645.788086 -20187.439453 -11715.820312 -21083.849609 -11700.274414   

              5             6             7             8             9  \
0 -22351.068359 -12944.652344 -22500.037109 -12917.988281 -22588.484375   
1 -17208.228516 -10970.005859 -17275.349609 -10986.038086 -17312.966797   
2 -20015.775391 -11398.946289 -20131.134766 -11407.384766 -20198.433594   
3 -19897.541016 -11707.235352 -20006.583984 -11713.375977 -20069.955078   
4 -19752.285156 -11208.695312 -19862.843750 -11219.630859 -19927.177734   
5 -20939.419922 -11854.429688 -21074.720703 -11853.963867 -21154.421875   
6 -18271.324219 -11410.683594 -18351.472656 -11423.217773 -18397.046875   
7 -19503.884766 -11337.875977 -19607.480469 -11348.257812 -19667.496094   
8 -21640.589844 -11589.904297 -21807.843750 -11588.563477 -21907.646484   
9 -21392.232422 -11691.321289 -21546.757812 -11690.004883 -21638.494141   

             10            11            12            13            14  \
0 -12904.922852 -22646.224609 -12900.262695 -22686.169922 -12901.164062   
1 -11003.162109 -17335.855469 -11021.026367 -17350.320312 -11039.407227   
2 -11418.796875 -20241.494141 -11432.240234 -20270.587891 -11447.106445   
3 -11723.364258 -20110.328125 -11735.851562 -20137.468750 -11750.034180   
4 -11232.775391 -19968.208984 -11247.494141 -19995.828125 -11263.341797   
5 -11859.028320 -21205.990234 -11867.716797 -21241.314453 -11878.881836   
6 -11437.884766 -18425.310547 -11453.928711 -18443.662109 -11470.907227   
7 -11361.156250 -19705.580078 -11375.768555 -19731.052734 -11391.572266   
8 -11592.247070 -21973.093750 -11599.516602 -22018.599609 -11609.356445   
9 -11694.033203 -21698.349609 -11701.731445 -21739.742188 -11712.010742   

             15            16            17            18            19  \
0 -22714.851562 -12905.937500 -22735.933594 -12913.522461 -22751.644531   
1 -17359.515625 -11058.158203 -17365.189453 -11077.182617 -17368.390625   
2 -20290.892578 -11463.000000 -20305.296875 -11479.657227 -20315.546875   
3 -20156.287109 -11765.416992 -20169.523438 -11781.679688 -20178.830078   
4 -20015.007812 -11280.013672 -20028.525391 -11297.303711 -20038.056641   
5 -21266.384766 -11891.809570 -21284.562500 -11906.036133 -21297.875000   
6 -18455.798828 -11488.542969 -18463.779297 -11506.660156 -18468.837891   
7 -19748.601562 -11408.233398 -19760.833984 -11425.531250 -19769.326172   
8 -22051.480469 -11621.090820 -22075.845703 -11634.250977 -22094.191406   
9 -21769.468750 -11724.155273 -21791.333984 -11737.693359 -21807.642578   

             20            21            22            23            24  \
0 -12923.213867 -22763.400391 -12934.522461 -22772.166016 -12947.102539   
1 -11096.413086 -17369.792969 -11115.806641 -17369.837891 -11135.327148   
2 -11496.895508 -20322.755859 -11514.585938 -20327.675781 -11532.635742   
3 -11798.603516 -20185.263672 -11816.040039 -20189.525391 -11833.879883   
4 -11315.066406 -20044.673828 -11333.199219 -20049.091797 -11351.625977   
5 -11921.246094 -21307.623047 -11937.216797 -21314.677734 -11953.788086   
6 -11525.139648 -18471.765625 -11543.897461 -18473.087891 -11562.875000   
7 -11443.310547 -19775.083984 -11461.465820 -19778.781250 -11479.916992   
8 -11648.509766 -22108.119141 -1166

In [20]:
# Construct the velocity dataframe from the raw simulator velocity output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
vel_m,vel_n,vel_r = stacked_raw_vel.shape
# Stack the XY or XYZ arrays of each body into columns, removing a dimension.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Had to add 1 to arange to go from 1 to 79 instead of 0.
vel_arr = np.column_stack(
    (np.repeat(np.arange(1, vel_m+1, 1),vel_n), 
     np.tile(np.arange(0,vel_n,1),vel_m), 
    stacked_raw_vel.reshape(vel_m*vel_n,-1))
)
# Create dataframe from stacked column array.
vel_df = pd.DataFrame(vel_arr)
# Delete intermediate numpy arrays and original data from memory.
del vel_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
vel_df = vel_df.groupby([0,1]).mean()
vel_df.index.names = ['time_step', 'body']
# Drop the time steps that could not be used for getting future data.
# Create list of time steps to drop.
beg_drop_index = max(vel_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(vel_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
vel_df.drop(drop_list, level=0, inplace=True)
# Create list of columns 
cols = ['vel_x', 'vel_y']
for i in range(1, num_ts_to_predict+1):
    cols.append('vel_x_' + str(i))
    cols.append('vel_y_' + str(i))
vel_df.columns = cols
# View final velocity dataframe with future time steps.
idx = pd.IndexSlice
vel_df.loc[idx[0:2,:], :]

vel_x         vel_y       vel_x_1       vel_y_1  \
time_step body                                                           
1.0       0.0  -13297.585938 -21158.062500 -13095.398438 -22052.777344   
          1.0  -10903.631836 -16621.818359 -10942.112305 -17066.871094   
          2.0  -11333.654297 -19078.960938 -11393.473633 -19781.359375   
          3.0  -11700.374023 -18999.427734 -11716.444336 -19674.957031   
          4.0  -11116.695312 -18852.402344 -11192.368164 -19527.167969   
          5.0  -11867.745117 -19856.552734 -11885.129883 -20666.884766   
          6.0  -11375.381836 -17585.041016 -11397.356445 -18104.480469   
          7.0  -11276.567383 -18649.560547 -11327.403320 -19291.912109   
          8.0  -11494.234375 -20361.787109 -11606.954102 -21308.888672   
          9.0  -11645.788086 -20187.439453 -11715.820312 -21083.849609   
2.0       0.0  -13095.398438 -22052.777344 -12995.507812 -22351.068359   
          1.0  -10942.112305 -17066.871094 -10955.525391 -17208.228516   
          2.0  -11393.473633 -19781.359375 -11394.704102 -20015.775391   
          3.0  -11716.444336 -19674.957031 -11707.301758 -19897.541016   
          4.0  -11192.368164 -19527.167969 -11200.546875 -19752.285156   
          5.0  -11885.129883 -20666.884766 -11863.637695 -20939.419922   
          6.0  -11397.356445 -18104.480469 -11401.579102 -18271.324219   
          7.0  -11327.403320 -19291.912109 -11331.137695 -19503.884766   
          8.0  -11606.954102 -21308.888672 -11597.722656 -21640.589844   
          9.0  -11715.820312 -21083.849609 -11700.274414 -21392.232422   

                     vel_x_2       vel_y_2       vel_x_3       vel_y_3  \
time_step body                                                           
1.0       0.0  -12995.507812 -22351.068359 -12944.652344 -22500.037109   
          1.0  -10955.525391 -17208.228516 -10970.005859 -17275.349609   
          2.0  -11394.704102 -20015.775391 -11398.946289 -20131.134766   
          3.0  -11707.301758 -19897.541016 -11707.235352 -20006.583984   
          4.0  -11200.546875 -19752.285156 -11208.695312 -19862.843750   
          5.0  -11863.637695 -20939.419922 -11854.429688 -21074.720703   
          6.0  -11401.579102 -18271.324219 -11410.683594 -18351.472656   
          7.0  -11331.137695 -19503.884766 -11337.875977 -19607.480469   
          8.0  -11597.722656 -21640.589844 -11589.904297 -21807.843750   
          9.0  -11700.274414 -21392.232422 -11691.321289 -21546.757812   
2.0       0.0  -12944.652344 -22500.037109 -12917.988281 -22588.484375   
          1.0  -10970.005859 -17275.349609 -10986.038086 -17312.966797   
          2.0  -11398.946289 -20131.134766 -11407.384766 -20198.433594   
          3.0  -11707.235352 -20006.583984 -11713.375977 -20069.955078   
          4.0  -11208.695312 -19862.843750 -11219.630859 -19927.177734   
          5.0  -11854.429688 -21074.720703 -11853.963867 -21154.421875   
          6.0  -11410.683594 -18351.472656 -11423.217773 -18397.046875   
          7.0  -11337.875977 -19607.480469 -11348.257812 -19667.496094   
          8.0  -11589.904297 -21807.843750 -11588.563477 -21907.646484   
          9.0  -11691.321289 -21546.757812 -11690.004883 -21638.494141   

                     vel_x_4       vel_y_4       vel_x_5       vel_y_5  \
time_step body                                                           
1.0       0.0  -12917.988281 -22588.484375 -12904.922852 -22646.224609   
          1.0  -10986.038086 -17312.966797 -11003.162109 -17335.855469   
          2.0  -11407.384766 -20198.433594 -11418.796875 -20241.494141   
          3.0  -11713.375977 -20069.955078 -11723.364258 -20110.328125   
          4.0  -11219.630859 -19927.177734 -11232.775391 -19968.208984   
          5.0  -11853.963867 -21154.421875 -11859.028320 -21205.990234   
          6.0  -11423.217773 -18397.046875 -11437.884766 -18425.310547   
          7.0  -11348.257812 -19667.496094 -11361.156250 -19705.580078   
          8.0  -11588.563

In [21]:
vel_df.shape

(399780, 42)

### Converting Displacement to Pandas DataFrame

In [22]:
# Stack all the satellites as bodies into a single numpy array.
stacked_raw_dis = np.stack(dis_list, axis=1)
stacked_raw_dis.shape

(39998, 10, 2)

In [23]:
# Create a numpy array with the same first 2 dimensions of the input data (time steps and num bodies)
# the number of columns will be the same as the number of time steps
# being predicted multiplied by the dimensions (2) (X and Y)
dis_pred_cache = np.full(
    (stacked_raw_dis.shape[0], stacked_raw_dis.shape[1], num_ts_to_predict*2),
    np.nan,
    dtype=np.float32
)
# Loop over all time steps in the numpy array.
# Grab groups of bodies from future time steps
for curr_time_step in tqdm(range(0, stacked_raw_dis.shape[0])):
    # Loop over the number of time steps in the future to be grabbing
    # velocities from.
    # Don't do last time steps for displacement dataframe.  Can only look so many
    # time steps into the future before running out of data.
    if curr_time_step < (stacked_raw_dis.shape[0] - num_ts_to_predict):
        for num_ts_in_future in range(1, num_ts_to_predict + 1):
            dis_pred_cache[int(curr_time_step), :, int(2*num_ts_in_future-2):int(2*num_ts_in_future)] = \
            stacked_raw_dis[int(curr_time_step + num_ts_in_future), :, 0:2]
            
# Concatenate the cached numpy array to the original displacement dataset
stacked_raw_dis = np.concatenate((stacked_raw_dis[:,:,0:2], dis_pred_cache), axis=2)
# Delete the cache.
del dis_pred_cache
gc.collect()
#Display first portion of the dataframe
pd.DataFrame(stacked_raw_dis[0])

100%|██████████| 39998/39998 [00:01<00:00, 31257.92it/s]


0           1           2           3           4           5  \
0 -47398912.0 -78458880.0 -46891008.0 -80109568.0 -46694400.0 -80814080.0   
1 -39387136.0 -60989440.0 -39403520.0 -61784064.0 -39501824.0 -62119936.0   
2 -41009152.0 -70479872.0 -41041920.0 -71778304.0 -41058304.0 -72339456.0   
3 -42205184.0 -70127616.0 -42172416.0 -71368704.0 -42123264.0 -71892992.0   
4 -40255488.0 -69595136.0 -40304640.0 -70836224.0 -40337408.0 -71372800.0   
5 -42844160.0 -73551872.0 -42729472.0 -75059200.0 -42696704.0 -75710464.0   
6 -41041920.0 -64643072.0 -41041920.0 -65585152.0 -41058304.0 -65970176.0   
7 -40779776.0 -68788224.0 -40796160.0 -69959680.0 -40812544.0 -70467584.0   
8 -41746432.0 -75710464.0 -41779200.0 -77512704.0 -41730048.0 -78303232.0   
9 -42188800.0 -74952704.0 -42139648.0 -76644352.0 -42123264.0 -77377536.0   

            6           7           8           9          10          11  \
0 -46563328.0 -81207296.0 -46481408.0 -81457152.0 -46465024.0 -81620992.0   
1 -39534592.0 -62279680.0 -39600128.0 -62386176.0 -39665664.0 -62443520.0   
2 -41058304.0 -72634368.0 -41107456.0 -72818688.0 -41140224.0 -72933376.0   
3 -42205184.0 -72171520.0 -42205184.0 -72355840.0 -42254336.0 -72462336.0   
4 -40402944.0 -71659520.0 -40435712.0 -71843840.0 -40484864.0 -71950336.0   
5 -42696704.0 -76058624.0 -42696704.0 -76283904.0 -42713088.0 -76427264.0   
6 -41140224.0 -66179072.0 -41172992.0 -66301952.0 -41222144.0 -66379776.0   
7 -40861696.0 -70725632.0 -40894464.0 -70901760.0 -40960000.0 -71004160.0   
8 -41713664.0 -78741504.0 -41713664.0 -79020032.0 -41779200.0 -79208448.0   
9 -42123264.0 -77783040.0 -42123264.0 -78036992.0 -42123264.0 -78209024.0   

           12          13          14          15          16          17  \
0 -46448640.0 -81743872.0 -46465024.0 -81825792.0 -46465024.0 -81891328.0   
1 -39714816.0 -62488576.0 -39796736.0 -62509056.0 -39862272.0 -62533632.0   
2 -41205760.0 -73027584.0 -41254912.0 -73080832.0 -41304064.0 -73129984.0   
3 -42270720.0 -72548352.0 -42352640.0 -72597504.0 -42401792.0 -72638464.0   
4 -40534016.0 -72036352.0 -40599552.0 -72089600.0 -40648704.0 -72130560.0   
5 -42762240.0 -76533760.0 -42795008.0 -76603392.0 -42860544.0 -76660736.0   
6 -41271296.0 -66433024.0 -41353216.0 -66465792.0 -41418752.0 -66486272.0   
7 -40976384.0 -71077888.0 -41058304.0 -71127040.0 -41123840.0 -71168000.0   
8 -41779200.0 -79347712.0 -41828352.0 -79446016.0 -41877504.0 -79523840.0   
9 -42139648.0 -78344192.0 -42205184.0 -78426112.0 -42254336.0 -78491648.0   

           18          19          20          21          22          23  \
0 -46546944.0 -81936384.0 -46530560.0 -81977344.0 -46628864.0 -81997824.0   
1 -39927808.0 -62529536.0 -39976960.0 -62533632.0 -40075264.0 -62529536.0   
2 -41385984.0 -73154560.0 -41435136.0 -73183232.0 -41500672.0 -73191424.0   
3 -42450944.0 -72663040.0 -42516480.0 -72687616.0 -42598400.0 -72687616.0   
4 -40730624.0 -72155136.0 -40779776.0 -72179712.0 -40861696.0 -72187904.0   
5 -42909696.0 -76697600.0 -42942464.0 -76734464.0 -43024384.0 -76746752.0   
6 -41467904.0 -66502656.0 -41533440.0 -66506752.0 -41615360.0 -66502656.0   
7 -41189376.0 -71188480.0 -41238528.0 -71208960.0 -41304064.0 -71213056.0   
8 -41943040.0 -79572992.0 -41959424.0 -79622144.0 -42041344.0 -79646720.0   
9 -42287104.0 -78540800.0 -42352640.0 -78581760.0 -42418176.0 -78602240.0   

           24          25          26          27          28          29  \
0 -46645248.0 -82022400.0 -46710784.0 -82026496.0 -46759936.0 -82046976.0   
1 -40157184.0 -62533632.0 -40222720.0 -62521344.0 -40288256.0 -62513152.0   
2 -41566208.0 -73203712.0 -41631744.0 -73199616.0 -41713664.0 -73203712.0   
3 -42663936.0 -72708096.0 -42713088.0 -72708096.0 -42778624.0 -72712192.0   
4 -40927232.0 -72200192.0 -40976384.0 -72196096.0 -41058304.0 -72200192.0   
5 -43089920.0 -76767232.0 -43155456.0 -76767232.0 -43204608.0 -76787712.0   
6 -41680896.0 -66506752.0 -41746432.0 -66502656.0 -41828352.0 -66498560.0   
7 -4

In [24]:
# Construct the displacement dataframe from the raw simulator displacement output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
dis_m,dis_n,dis_r = stacked_raw_dis.shape
# Stack the XY or XYZ arrays of each body into columns, removing a dimension.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Had to add 1 to arange to go from 1 to 79 instead of 0.
dis_arr = np.column_stack(
    (np.repeat(np.arange(1, dis_m+1, 1),dis_n), 
     np.tile(np.arange(0,dis_n,1),dis_m), 
     stacked_raw_dis.reshape(dis_m*dis_n,-1))
)
# Create dataframe from stacked column array.
dis_df = pd.DataFrame(dis_arr)
# Delete intermediate numpy arrays and original data from memory.
del dis_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
dis_df = dis_df.groupby([0,1]).mean()
dis_df.index.names = ['time_step', 'body']
# Drop the time steps that could not be used for getting future data.
# Create list of time steps to drop.
beg_drop_index = max(dis_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(dis_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
dis_df.drop(drop_list, level=0, inplace=True)
# Create list of columns 
cols = ['dis_x', 'dis_y']
for i in range(1, num_ts_to_predict+1):
    cols.append('dis_x_' + str(i))
    cols.append('dis_y_' + str(i))
dis_df.columns = cols
# Drop dis_x and dis_y columns since we won't need then for ML training input.
dis_df.drop(['dis_x', 'dis_y'], axis=1,inplace=True)
# View final velocity dataframe with future time steps.
idx = pd.IndexSlice
dis_df.loc[idx[0:2,:], :]

dis_x_1     dis_y_1     dis_x_2     dis_y_2     dis_x_3  \
time_step body                                                               
1.0       0.0  -46891008.0 -80109568.0 -46694400.0 -80814080.0 -46563328.0   
          1.0  -39403520.0 -61784064.0 -39501824.0 -62119936.0 -39534592.0   
          2.0  -41041920.0 -71778304.0 -41058304.0 -72339456.0 -41058304.0   
          3.0  -42172416.0 -71368704.0 -42123264.0 -71892992.0 -42205184.0   
          4.0  -40304640.0 -70836224.0 -40337408.0 -71372800.0 -40402944.0   
          5.0  -42729472.0 -75059200.0 -42696704.0 -75710464.0 -42696704.0   
          6.0  -41041920.0 -65585152.0 -41058304.0 -65970176.0 -41140224.0   
          7.0  -40796160.0 -69959680.0 -40812544.0 -70467584.0 -40861696.0   
          8.0  -41779200.0 -77512704.0 -41730048.0 -78303232.0 -41713664.0   
          9.0  -42139648.0 -76644352.0 -42123264.0 -77377536.0 -42123264.0   
2.0       0.0  -46694400.0 -80814080.0 -46563328.0 -81207296.0 -46481408.0   
          1.0  -39501824.0 -62119936.0 -39534592.0 -62279680.0 -39600128.0   
          2.0  -41058304.0 -72339456.0 -41058304.0 -72634368.0 -41107456.0   
          3.0  -42123264.0 -71892992.0 -42205184.0 -72171520.0 -42205184.0   
          4.0  -40337408.0 -71372800.0 -40402944.0 -71659520.0 -40435712.0   
          5.0  -42696704.0 -75710464.0 -42696704.0 -76058624.0 -42696704.0   
          6.0  -41058304.0 -65970176.0 -41140224.0 -66179072.0 -41172992.0   
          7.0  -40812544.0 -70467584.0 -40861696.0 -70725632.0 -40894464.0   
          8.0  -41730048.0 -78303232.0 -41713664.0 -78741504.0 -41713664.0   
          9.0  -42123264.0 -77377536.0 -42123264.0 -77783040.0 -42123264.0   

                   dis_y_3     dis_x_4     dis_y_4     dis_x_5     dis_y_5  \
time_step body                                                               
1.0       0.0  -81207296.0 -46481408.0 -81457152.0 -46465024.0 -81620992.0   
          1.0  -62279680.0 -39600128.0 -62386176.0 -39665664.0 -62443520.0   
          2.0  -72634368.0 -41107456.0 -72818688.0 -41140224.0 -72933376.0   
          3.0  -72171520.0 -42205184.0 -72355840.0 -42254336.0 -72462336.0   
          4.0  -71659520.0 -40435712.0 -71843840.0 -40484864.0 -71950336.0   
          5.0  -76058624.0 -42696704.0 -76283904.0 -42713088.0 -76427264.0   
          6.0  -66179072.0 -41172992.0 -66301952.0 -41222144.0 -66379776.0   
          7.0  -70725632.0 -40894464.0 -70901760.0 -40960000.0 -71004160.0   
          8.0  -78741504.0 -41713664.0 -79020032.0 -41779200.0 -79208448.0   
          9.0  -77783040.0 -42123264.0 -78036992.0 -42123264.0 -78209024.0   
2.0       0.0  -81457152.0 -46465024.0 -81620992.0 -46448640.0 -81743872.0   
          1.0  -62386176.0 -39665664.0 -62443520.0 -39714816.0 -62488576.0   
          2.0  -72818688.0 -41140224.0 -72933376.0 -41205760.0 -73027584.0   
          3.0  -72355840.0 -42254336.0 -72462336.0 -42270720.0 -72548352.0   
          4.0  -71843840.0 -40484864.0 -71950336.0 -40534016.0 -72036352.0   
          5.0  -76283904.0 -42713088.0 -76427264.0 -42762240.0 -76533760.0   
          6.0  -66301952.0 -41222144.0 -66379776.0 -41271296.0 -66433024.0   
          7.0  -70901760.0 -40960000.0 -71004160.0 -40976384.0 -71077888.0   
          8.0  -79020032.0 -41779200.0 -79208448.0 -41779200.0 -79347712.0   
          9.0  -78036992.0 -42123264.0 -78209024.0 -42139648.0 -78344192.0   

                   dis_x_6     dis_y_6     dis_x_7     dis_y_7     dis_x_8  \
time_step body                                                               
1.0       0.0  -46448640.0 -81743872.0 -46465024.0 -81825792.0 -46465024.0   
          1.0  -39714816.0 -62488576.0 -39796736.0 -62509056.0 -39862272.0   
          2.0  -41205760.0 -73027584.0 -41254912.0 -73080832.0 -41304064.0   
          3.0  -42270720.0 -72548352.0 -42352640.0 -72597504.0 -42401792.0   
          4.0  -40534016.0 -72036352.0 -40599552.0 -72089600.0 -40648704.0   
          5.0  -42762240.0 -76533760.0 

In [25]:
dis_df.shape

(399780, 40)

### Converting Mass to Pandas DataFrame

In [26]:
stacked_raw_mass = np.array(mass_list)
stacked_raw_mass

array([ 442., 1643., 3794., 1969.,  223., 2652., 1338., 2512., 1422.,
       3110.], dtype=float32)

In [27]:
# Construct the mass dataframe from the raw simulator mass output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
mass_n = stacked_raw_mass.shape[0]
# Stack the Mass column with the indexing columns.  Mass column will be repeated by the number
# of time steps.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Using displacement dataframe dimensions to copy the masses enough.
mass_arr = np.column_stack(
     (np.repeat(np.arange(1, dis_m+1, 1),mass_n), 
     np.tile(np.arange(0,mass_n,1), dis_m),
     np.tile(stacked_raw_mass.reshape(mass_n,), dis_m))
)
# Create dataframe from stacked column array.
mass_df = pd.DataFrame(mass_arr)
# Delete intermediate numpy arrays and original data from memory.
del mass_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
mass_df = mass_df.groupby([0,1]).mean()
mass_df.index.names = ['time_step', 'body']
mass_df.columns = ['mass']
# Drop the time steps that could not be used for getting future data.
# Create list of time steps to drop.
beg_drop_index = max(mass_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(mass_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
mass_df.drop(drop_list, axis=0, inplace=True)
mass_df.head(15)

mass
time_step body        
1.0       0.0    442.0
          1.0   1643.0
          2.0   3794.0
          3.0   1969.0
          4.0    223.0
          5.0   2652.0
          6.0   1338.0
          7.0   2512.0
          8.0   1422.0
          9.0   3110.0
2.0       0.0    442.0
          1.0   1643.0
          2.0   3794.0
          3.0   1969.0
          4.0    223.0

In [28]:
mass_df.shape

(399780, 1)

# Merge the Mass, Acceleration, Velocity, and Displacement Data

In [29]:
# Copy mass dataframe to start creating merged version.  Delete mass df afterwards.
merged_data = mass_df.copy(deep=True)
merged_data = pd.merge(merged_data, acc_df, left_index=True, right_index=True, how='outer')
# Delete mass_df and acc_df
del mass_df
del acc_df
gc.collect()
merged_data.head(15)

mass     acc_x     acc_y
time_step body                            
1.0       0.0    442.0  0.054972 -0.624254
          1.0   1643.0 -0.050005 -0.317740
          2.0   3794.0 -0.104679 -0.475992
          3.0   1969.0 -0.066227 -0.467194
          4.0    223.0 -0.112355 -0.456318
          5.0   2652.0 -0.092108 -0.547595
          6.0   1338.0 -0.046654 -0.368221
          7.0   2512.0 -0.087844 -0.441338
          8.0   1422.0 -0.189189 -0.602040
          9.0   3110.0 -0.148280 -0.585344
2.0       0.0    442.0  0.042107 -0.137894
          1.0   1643.0 -0.004415 -0.067007
          2.0   3794.0 -0.001965 -0.108939
          3.0   1969.0  0.003527 -0.103828
          4.0    223.0 -0.004888 -0.104684

In [30]:
# Merge in the velocity data.
merged_data = pd.merge(merged_data, vel_df, left_index=True, right_index=True, how='outer')
del vel_df
gc.collect()
merged_data.head(15)

mass     acc_x     acc_y         vel_x         vel_y  \
time_step body                                                           
1.0       0.0    442.0  0.054972 -0.624254 -13297.585938 -21158.062500   
          1.0   1643.0 -0.050005 -0.317740 -10903.631836 -16621.818359   
          2.0   3794.0 -0.104679 -0.475992 -11333.654297 -19078.960938   
          3.0   1969.0 -0.066227 -0.467194 -11700.374023 -18999.427734   
          4.0    223.0 -0.112355 -0.456318 -11116.695312 -18852.402344   
          5.0   2652.0 -0.092108 -0.547595 -11867.745117 -19856.552734   
          6.0   1338.0 -0.046654 -0.368221 -11375.381836 -17585.041016   
          7.0   2512.0 -0.087844 -0.441338 -11276.567383 -18649.560547   
          8.0   1422.0 -0.189189 -0.602040 -11494.234375 -20361.787109   
          9.0   3110.0 -0.148280 -0.585344 -11645.788086 -20187.439453   
2.0       0.0    442.0  0.042107 -0.137894 -13095.398438 -22052.777344   
          1.0   1643.0 -0.004415 -0.067007 -10942.112305 -17066.871094   
          2.0   3794.0 -0.001965 -0.108939 -11393.473633 -19781.359375   
          3.0   1969.0  0.003527 -0.103828 -11716.444336 -19674.957031   
          4.0    223.0 -0.004888 -0.104684 -11192.368164 -19527.167969   

                     vel_x_1       vel_y_1       vel_x_2       vel_y_2  \
time_step body                                                           
1.0       0.0  -13095.398438 -22052.777344 -12995.507812 -22351.068359   
          1.0  -10942.112305 -17066.871094 -10955.525391 -17208.228516   
          2.0  -11393.473633 -19781.359375 -11394.704102 -20015.775391   
          3.0  -11716.444336 -19674.957031 -11707.301758 -19897.541016   
          4.0  -11192.368164 -19527.167969 -11200.546875 -19752.285156   
          5.0  -11885.129883 -20666.884766 -11863.637695 -20939.419922   
          6.0  -11397.356445 -18104.480469 -11401.579102 -18271.324219   
          7.0  -11327.403320 -19291.912109 -11331.137695 -19503.884766   
          8.0  -11606.954102 -21308.888672 -11597.722656 -21640.589844   
          9.0  -11715.820312 -21083.849609 -11700.274414 -21392.232422   
2.0       0.0  -12995.507812 -22351.068359 -12944.652344 -22500.037109   
          1.0  -10955.525391 -17208.228516 -10970.005859 -17275.349609   
          2.0  -11394.704102 -20015.775391 -11398.946289 -20131.134766   
          3.0  -11707.301758 -19897.541016 -11707.235352 -20006.583984   
          4.0  -11200.546875 -19752.285156 -11208.695312 -19862.843750   

                     vel_x_3       vel_y_3       vel_x_4       vel_y_4  \
time_step body                                                           
1.0       0.0  -12944.652344 -22500.037109 -12917.988281 -22588.484375   
          1.0  -10970.005859 -17275.349609 -10986.038086 -17312.966797   
          2.0  -11398.946289 -20131.134766 -11407.384766 -20198.433594   
          3.0  -11707.235352 -20006.583984 -11713.375977 -20069.955078   
          4.0  -11208.695312 -19862.843750 -11219.630859 -19927.177734   
          5.0  -11854.429688 -21074.720703 -11853.963867 -21154.421875   
          6.0  -11410.683594 -18351.472656 -11423.217773 -18397.046875   
          7.0  -11337.875977 -19607.480469 -11348.257812 -19667.496094   
          8.0  -11589.904297 -21807.843750 -11588.563477 -21907.646484   
          9.0  -11691.321289 -21546.757812 -11690.004883 -21638.494141   
2.0       0.0  -12917.988281 -22588.484375 -12904.922852 -22646.224609   
          1.0  -10986.038086 -17312.966797 -11003.162109 -17335.855469   
          2.0  -11407.384766 -20198.433594 -11418.796875 -20241.494141   
          3.0  -11713.375977 -20069.955078 -11723.364258 -20110.328125   
          4.0  -11219.630859 -19927.177734 -11232.775391 -19968.208984   

                     vel_x_5       vel_y_5       vel_x_6       vel_y_6  \
time_step body                                                           
1.0       0.0  -12904.922852 -22646.224609 -12900.262695 -22686.169922   
          1.0  -110

In [31]:
# Merge in the displacement data
merged_data = pd.merge(merged_data, dis_df, left_index=True, right_index=True, how='outer')
del dis_df
gc.collect()
merged_data.head(15)

mass     acc_x     acc_y         vel_x         vel_y  \
time_step body                                                           
1.0       0.0    442.0  0.054972 -0.624254 -13297.585938 -21158.062500   
          1.0   1643.0 -0.050005 -0.317740 -10903.631836 -16621.818359   
          2.0   3794.0 -0.104679 -0.475992 -11333.654297 -19078.960938   
          3.0   1969.0 -0.066227 -0.467194 -11700.374023 -18999.427734   
          4.0    223.0 -0.112355 -0.456318 -11116.695312 -18852.402344   
          5.0   2652.0 -0.092108 -0.547595 -11867.745117 -19856.552734   
          6.0   1338.0 -0.046654 -0.368221 -11375.381836 -17585.041016   
          7.0   2512.0 -0.087844 -0.441338 -11276.567383 -18649.560547   
          8.0   1422.0 -0.189189 -0.602040 -11494.234375 -20361.787109   
          9.0   3110.0 -0.148280 -0.585344 -11645.788086 -20187.439453   
2.0       0.0    442.0  0.042107 -0.137894 -13095.398438 -22052.777344   
          1.0   1643.0 -0.004415 -0.067007 -10942.112305 -17066.871094   
          2.0   3794.0 -0.001965 -0.108939 -11393.473633 -19781.359375   
          3.0   1969.0  0.003527 -0.103828 -11716.444336 -19674.957031   
          4.0    223.0 -0.004888 -0.104684 -11192.368164 -19527.167969   

                     vel_x_1       vel_y_1       vel_x_2       vel_y_2  \
time_step body                                                           
1.0       0.0  -13095.398438 -22052.777344 -12995.507812 -22351.068359   
          1.0  -10942.112305 -17066.871094 -10955.525391 -17208.228516   
          2.0  -11393.473633 -19781.359375 -11394.704102 -20015.775391   
          3.0  -11716.444336 -19674.957031 -11707.301758 -19897.541016   
          4.0  -11192.368164 -19527.167969 -11200.546875 -19752.285156   
          5.0  -11885.129883 -20666.884766 -11863.637695 -20939.419922   
          6.0  -11397.356445 -18104.480469 -11401.579102 -18271.324219   
          7.0  -11327.403320 -19291.912109 -11331.137695 -19503.884766   
          8.0  -11606.954102 -21308.888672 -11597.722656 -21640.589844   
          9.0  -11715.820312 -21083.849609 -11700.274414 -21392.232422   
2.0       0.0  -12995.507812 -22351.068359 -12944.652344 -22500.037109   
          1.0  -10955.525391 -17208.228516 -10970.005859 -17275.349609   
          2.0  -11394.704102 -20015.775391 -11398.946289 -20131.134766   
          3.0  -11707.301758 -19897.541016 -11707.235352 -20006.583984   
          4.0  -11200.546875 -19752.285156 -11208.695312 -19862.843750   

                     vel_x_3       vel_y_3       vel_x_4       vel_y_4  \
time_step body                                                           
1.0       0.0  -12944.652344 -22500.037109 -12917.988281 -22588.484375   
          1.0  -10970.005859 -17275.349609 -10986.038086 -17312.966797   
          2.0  -11398.946289 -20131.134766 -11407.384766 -20198.433594   
          3.0  -11707.235352 -20006.583984 -11713.375977 -20069.955078   
          4.0  -11208.695312 -19862.843750 -11219.630859 -19927.177734   
          5.0  -11854.429688 -21074.720703 -11853.963867 -21154.421875   
          6.0  -11410.683594 -18351.472656 -11423.217773 -18397.046875   
          7.0  -11337.875977 -19607.480469 -11348.257812 -19667.496094   
          8.0  -11589.904297 -21807.843750 -11588.563477 -21907.646484   
          9.0  -11691.321289 -21546.757812 -11690.004883 -21638.494141   
2.0       0.0  -12917.988281 -22588.484375 -12904.922852 -22646.224609   
          1.0  -10986.038086 -17312.966797 -11003.162109 -17335.855469   
          2.0  -11407.384766 -20198.433594 -11418.796875 -20241.494141   
          3.0  -11713.375977 -20069.955078 -11723.364258 -20110.328125   
          4.0  -11219.630859 -19927.177734 -11232.775391 -19968.208984   

                     vel_x_5       vel_y_5       vel_x_6       vel_y_6  \
time_step body                                                           
1.0       0.0  -12904.922852 -22646.224609 -12900.262695 -22686.169922   
          1.0  -110

In [32]:
# Rearrange columns so they are in the needed order.
# Create list of what the column order should be.
cols = []
cols.extend(['mass', 'acc_x', 'acc_y', 'vel_x', 'vel_y'])
# Loop over all the time steps we wanted to predict and rearrange the columns
# accordingly
for i in range(1,num_ts_to_predict+1):
    cols.append('dis_x_' + str(i))
    cols.append('dis_y_' + str(i))
    cols.append('vel_x_' + str(i))
    cols.append('vel_y_' + str(i))
# Rearrange columns using the create columns list.
merged_data = merged_data[cols]
merged_data.head(15)

mass     acc_x     acc_y         vel_x         vel_y  \
time_step body                                                           
1.0       0.0    442.0  0.054972 -0.624254 -13297.585938 -21158.062500   
          1.0   1643.0 -0.050005 -0.317740 -10903.631836 -16621.818359   
          2.0   3794.0 -0.104679 -0.475992 -11333.654297 -19078.960938   
          3.0   1969.0 -0.066227 -0.467194 -11700.374023 -18999.427734   
          4.0    223.0 -0.112355 -0.456318 -11116.695312 -18852.402344   
          5.0   2652.0 -0.092108 -0.547595 -11867.745117 -19856.552734   
          6.0   1338.0 -0.046654 -0.368221 -11375.381836 -17585.041016   
          7.0   2512.0 -0.087844 -0.441338 -11276.567383 -18649.560547   
          8.0   1422.0 -0.189189 -0.602040 -11494.234375 -20361.787109   
          9.0   3110.0 -0.148280 -0.585344 -11645.788086 -20187.439453   
2.0       0.0    442.0  0.042107 -0.137894 -13095.398438 -22052.777344   
          1.0   1643.0 -0.004415 -0.067007 -10942.112305 -17066.871094   
          2.0   3794.0 -0.001965 -0.108939 -11393.473633 -19781.359375   
          3.0   1969.0  0.003527 -0.103828 -11716.444336 -19674.957031   
          4.0    223.0 -0.004888 -0.104684 -11192.368164 -19527.167969   

                   dis_x_1     dis_y_1       vel_x_1       vel_y_1  \
time_step body                                                       
1.0       0.0  -46891008.0 -80109568.0 -13095.398438 -22052.777344   
          1.0  -39403520.0 -61784064.0 -10942.112305 -17066.871094   
          2.0  -41041920.0 -71778304.0 -11393.473633 -19781.359375   
          3.0  -42172416.0 -71368704.0 -11716.444336 -19674.957031   
          4.0  -40304640.0 -70836224.0 -11192.368164 -19527.167969   
          5.0  -42729472.0 -75059200.0 -11885.129883 -20666.884766   
          6.0  -41041920.0 -65585152.0 -11397.356445 -18104.480469   
          7.0  -40796160.0 -69959680.0 -11327.403320 -19291.912109   
          8.0  -41779200.0 -77512704.0 -11606.954102 -21308.888672   
          9.0  -42139648.0 -76644352.0 -11715.820312 -21083.849609   
2.0       0.0  -46694400.0 -80814080.0 -12995.507812 -22351.068359   
          1.0  -39501824.0 -62119936.0 -10955.525391 -17208.228516   
          2.0  -41058304.0 -72339456.0 -11394.704102 -20015.775391   
          3.0  -42123264.0 -71892992.0 -11707.301758 -19897.541016   
          4.0  -40337408.0 -71372800.0 -11200.546875 -19752.285156   

                   dis_x_2     dis_y_2       vel_x_2       vel_y_2  \
time_step body                                                       
1.0       0.0  -46694400.0 -80814080.0 -12995.507812 -22351.068359   
          1.0  -39501824.0 -62119936.0 -10955.525391 -17208.228516   
          2.0  -41058304.0 -72339456.0 -11394.704102 -20015.775391   
          3.0  -42123264.0 -71892992.0 -11707.301758 -19897.541016   
          4.0  -40337408.0 -71372800.0 -11200.546875 -19752.285156   
          5.0  -42696704.0 -75710464.0 -11863.637695 -20939.419922   
          6.0  -41058304.0 -65970176.0 -11401.579102 -18271.324219   
          7.0  -40812544.0 -70467584.0 -11331.137695 -19503.884766   
          8.0  -41730048.0 -78303232.0 -11597.722656 -21640.589844   
          9.0  -42123264.0 -77377536.0 -11700.274414 -21392.232422   
2.0       0.0  -46563328.0 -81207296.0 -12944.652344 -22500.037109   
          1.0  -39534592.0 -62279680.0 -10970.005859 -17275.349609   
          2.0  -41058304.0 -72634368.0 -11398.946289 -20131.134766   
          3.0  -42205184.0 -72171520.0 -11707.235352 -20006.583984   
          4.0  -40402944.0 -71659520.0 -11208.695312 -19862.843750   

                   dis_x_3     dis_y_3       vel_x_3       vel_y_3  \
time_step body                                                       
1.0       0.0  -46563328.0 -81207296.0 -12944.652344 -22500.037109   
          1.0  -39534592.0 -62279680.0 -10970.005859 -17275.349609   
          2.0  -41058304.0 -72634368.0 -11398.946289 -20131.134766   
          3.0  -42205184.0 

# Create Body Time Series Data Format

In [33]:
merged_data_time_series = merged_data.copy(deep=True)
merged_data_time_series = merged_data_time_series.swaplevel('time_step', 'body').sort_index(level=0)
merged_data_time_series.head(15)

mass     acc_x     acc_y         vel_x         vel_y  \
body time_step                                                          
0.0  1.0        442.0  0.054972 -0.624254 -13297.585938 -21158.062500   
     2.0        442.0  0.042107 -0.137894 -13095.398438 -22052.777344   
     3.0        442.0  0.020567 -0.059235 -12995.507812 -22351.068359   
     4.0        442.0  0.010745 -0.032574 -12944.652344 -22500.037109   
     5.0        442.0  0.005574 -0.020325 -12917.988281 -22588.484375   
     6.0        442.0  0.002527 -0.013664 -12904.922852 -22646.224609   
     7.0        442.0  0.000580 -0.009630 -12900.262695 -22686.169922   
     8.0        442.0 -0.000740 -0.006996 -12901.164062 -22714.851562   
     9.0        442.0 -0.001677 -0.005179 -12905.937500 -22735.933594   
     10.0       442.0 -0.002367 -0.003873 -12913.522461 -22751.644531   
     11.0       442.0 -0.002890 -0.002898 -12923.213867 -22763.400391   
     12.0       442.0 -0.003296 -0.002152 -12934.522461 -22772.166016   
     13.0       442.0 -0.003617 -0.001568 -12947.102539 -22778.611328   
     14.0       442.0 -0.003876 -0.001101 -12960.699219 -22783.216797   
     15.0       442.0 -0.004088 -0.000722 -12975.123047 -22786.341797   

                   dis_x_1     dis_y_1       vel_x_1       vel_y_1  \
body time_step                                                       
0.0  1.0       -46891008.0 -80109568.0 -13095.398438 -22052.777344   
     2.0       -46694400.0 -80814080.0 -12995.507812 -22351.068359   
     3.0       -46563328.0 -81207296.0 -12944.652344 -22500.037109   
     4.0       -46481408.0 -81457152.0 -12917.988281 -22588.484375   
     5.0       -46465024.0 -81620992.0 -12904.922852 -22646.224609   
     6.0       -46448640.0 -81743872.0 -12900.262695 -22686.169922   
     7.0       -46465024.0 -81825792.0 -12901.164062 -22714.851562   
     8.0       -46465024.0 -81891328.0 -12905.937500 -22735.933594   
     9.0       -46546944.0 -81936384.0 -12913.522461 -22751.644531   
     10.0      -46530560.0 -81977344.0 -12923.213867 -22763.400391   
     11.0      -46628864.0 -81997824.0 -12934.522461 -22772.166016   
     12.0      -46645248.0 -82022400.0 -12947.102539 -22778.611328   
     13.0      -46710784.0 -82026496.0 -12960.699219 -22783.216797   
     14.0      -46759936.0 -82046976.0 -12975.123047 -22786.341797   
     15.0      -46792704.0 -82046976.0 -12990.230469 -22788.253906   

                   dis_x_2     dis_y_2       vel_x_2       vel_y_2  \
body time_step                                                       
0.0  1.0       -46694400.0 -80814080.0 -12995.507812 -22351.068359   
     2.0       -46563328.0 -81207296.0 -12944.652344 -22500.037109   
     3.0       -46481408.0 -81457152.0 -12917.988281 -22588.484375   
     4.0       -46465024.0 -81620992.0 -12904.922852 -22646.224609   
     5.0       -46448640.0 -81743872.0 -12900.262695 -22686.169922   
     6.0       -46465024.0 -81825792.0 -12901.164062 -22714.851562   
     7.0       -46465024.0 -81891328.0 -12905.937500 -22735.933594   
     8.0       -46546944.0 -81936384.0 -12913.522461 -22751.644531   
     9.0       -46530560.0 -81977344.0 -12923.213867 -22763.400391   
     10.0      -46628864.0 -81997824.0 -12934.522461 -22772.166016   
     11.0      -46645248.0 -82022400.0 -12947.102539 -22778.611328   
     12.0      -46710784.0 -82026496.0 -12960.699219 -22783.216797   
     13.0      -46759936.0 -82046976.0 -12975.123047 -22786.341797   
     14.0      -46792704.0 -82046976.0 -12990.230469 -22788.253906   
     15.0      -46874624.0 -82051072.0 -13005.905273 -22789.156250   

                   dis_x_3     dis_y_3       vel_x_3       vel_y_3  \
body time_step                                                       
0.0  1.0       -46563328.0 -81207296.0 -12944.652344 -22500.037109   
     2.0       -46481408.0 -81457152.0 -12917.988281 -22588.484375   
     3.0       -46465024.0 -81620992.0 -12904.922852 -22646.224609   
     4.0       -46448640.0 -81743872.0 -129

# Attempt Converting Merged Datasets to Numpy Arrays and Save as Both Pd dataframes and Np Arrays

In [34]:
merged_data.to_numpy().shape

(399780, 85)

In [35]:
dim0 = len(merged_data.index.get_level_values(0).unique())
dim1 = len(merged_data.index.get_level_values(1).unique())
dim2 = merged_data.shape[1]
merged_data_ndarray = merged_data.to_numpy().reshape((dim0, dim1, dim2))
merged_data_ndarray[0,0]

array([ 4.42000000e+02,  5.49721643e-02, -6.24254346e-01, -1.32975859e+04,
       -2.11580625e+04, -4.68910080e+07, -8.01095680e+07, -1.30953984e+04,
       -2.20527773e+04, -4.66944000e+07, -8.08140800e+07, -1.29955078e+04,
       -2.23510684e+04, -4.65633280e+07, -8.12072960e+07, -1.29446523e+04,
       -2.25000371e+04, -4.64814080e+07, -8.14571520e+07, -1.29179883e+04,
       -2.25884844e+04, -4.64650240e+07, -8.16209920e+07, -1.29049229e+04,
       -2.26462246e+04, -4.64486400e+07, -8.17438720e+07, -1.29002627e+04,
       -2.26861699e+04, -4.64650240e+07, -8.18257920e+07, -1.29011641e+04,
       -2.27148516e+04, -4.64650240e+07, -8.18913280e+07, -1.29059375e+04,
       -2.27359336e+04, -4.65469440e+07, -8.19363840e+07, -1.29135225e+04,
       -2.27516445e+04, -4.65305600e+07, -8.19773440e+07, -1.29232139e+04,
       -2.27634004e+04, -4.66288640e+07, -8.19978240e+07, -1.29345225e+04,
       -2.27721660e+04, -4.66452480e+07, -8.20224000e+07, -1.29471025e+04,
       -2.27786113e+04, -

In [36]:
dim0 = len(merged_data_time_series.index.get_level_values(0).unique())
dim1 = len(merged_data_time_series.index.get_level_values(1).unique())
dim2 = merged_data.shape[1]
merged_data_time_series_ndarray = merged_data_time_series.to_numpy().reshape((dim0, dim1, dim2))
merged_data_time_series_ndarray[0,5]

array([ 4.42000000e+02,  2.52668746e-03, -1.36639830e-02, -1.29049229e+04,
       -2.26462246e+04, -4.64486400e+07, -8.17438720e+07, -1.29002627e+04,
       -2.26861699e+04, -4.64650240e+07, -8.18257920e+07, -1.29011641e+04,
       -2.27148516e+04, -4.64650240e+07, -8.18913280e+07, -1.29059375e+04,
       -2.27359336e+04, -4.65469440e+07, -8.19363840e+07, -1.29135225e+04,
       -2.27516445e+04, -4.65305600e+07, -8.19773440e+07, -1.29232139e+04,
       -2.27634004e+04, -4.66288640e+07, -8.19978240e+07, -1.29345225e+04,
       -2.27721660e+04, -4.66452480e+07, -8.20224000e+07, -1.29471025e+04,
       -2.27786113e+04, -4.67107840e+07, -8.20264960e+07, -1.29606992e+04,
       -2.27832168e+04, -4.67599360e+07, -8.20469760e+07, -1.29751230e+04,
       -2.27863418e+04, -4.67927040e+07, -8.20469760e+07, -1.29902305e+04,
       -2.27882539e+04, -4.68746240e+07, -8.20510720e+07, -1.30059053e+04,
       -2.27891562e+04, -4.69401600e+07, -8.20469760e+07, -1.30220605e+04,
       -2.27892109e+04, -

## Save the Numpy Arrays and Pandas Dataframes

In [37]:
# Set the output directory.
out_dir = 'output/'

Save the dataframes by pickling them.

In [38]:
# Save using 'default' as the key.
# https://pythontic.com/pandas/serialization/hdf5

#merged_data.to_hdf(out_dir + 'sim_data_df-ts-body.hdf5', 'default')

file_name = '1-hour_10-sats_predict-20-steps_720ts_200000steps_5freq.hdf5'
merged_data_time_series.to_hdf(out_dir + file_name, 'default')

# merged_data.to_pickle(out_dir + 'sim_data_df-ts-body.pkl')
# merged_data_time_series.to_pickle(out_dir + 'sim_data_df-body-ts.pkl')

Save the dataframes to XLSX files to view in Excel. \
Some larger datasets can't be saved to Excel.  Takes forever to parse the file.

In [ ]:
# merged_data.to_excel(out_dir + 'sim_data_df-ts-body.xlsx')
# merged_data_time_series.to_excel(out_dir + 'sim_data_df-body-ts.xlsx')

Save the numpy arrays by using numpy's saving function.

In [ ]:
#np.save(out_dir + 'sim_data_np-ts-body.npy', merged_data_ndarray)
#np.save(out_dir + 'sim_data_np-body-ts.npy', merged_data_time_series_ndarray)